Ujednoznacznianie wypowiedzi użytkownika
========================================

Problem
-------
W systemie dialogowym ukierunkowanym na wypełnianie wielu zadań jednocześnie polecenia użytkownika mogą być niejednoznacznie. Przykładowo wypowiedź

> please book it for me

może dotyczyć zarówno rezerwacji pokoju w hotelu jak i biletu na pociąg.

System, w którym moduł NLU jest zbudowany z wykorzystaniem gramatyk semantycznych może zwrócić
więcej niż jedną ramę reprezentującą znaczenie wypowiedzi. Która rama powinna zostać uznana za
prawidłową?

System, w którym moduł NLU jest zbudowany przy użyciu modelu sekwencyjnego może zwrócić jedną,
arbitralnie wybraną ramę. Co wtedy?

Ujednoznacznianie z wykorzystaniem reguł
----------------------------------------

Do ujednoznaczniania wypowiedzi użytkownika można wykorzystać monitor stanu dialogu oraz taktykę
prowadzenia dialogu.  Możemy m.in.:

 1. Dopasować niejednoznaczną wypowiedź do wszystkich dziedzin licząc na to, że w toku dialogu
    niejednoznaczność zostanie rozstrzygnięta (to
    rozwiązanie zostało przyjęte w monitorze `SimpleRuleDST` przedstawionym na zajęciach ósmych).

 2. Dopasować niejednoznaczną wypowiedź wyłącznie do tej dziedziny, dla której stan dialogu zawiera
    wypełnione sloty.

 3. Sprawdzić czy wypowiedź użytkownika stanowi odpowiedź na pytanie uprzednio zadane przez system
    (pole `request_state` w monitorze `SimpleRuleDST`).

 4. Wykorzystać taktykę prowadzenia dialogu do zadania pytania, które rozstrzygnie
    niejednoznaczność.

Ujednoznacznianie z wykorzystaniem uczenia maszynowego
------------------------------------------------------

W procesie uczenia modelu NLU można wykorzystać historię dialogu jako kontekst (zbiór dodatkowych
cech) warunkujących wynik uczenia.
Takie podejście zostało zastosowane w modelu [jointBERT](https://github.com/thu-coai/ConvLab-2/blob/master/convlab2/nlu/jointBERT/jointBERT.py), w którym kontekst składa się z trzech (sklejonych ze sobą) tur dialogu poprzedzających bieżącą wypowiedź.

Porównajmy skuteczność modelu bezkontekstowego ze skutecznością modelu uwzględniającego kontekst.
Do oceny jakości wykorzystamy zbiór danych [MultiWOZ](https://github.com/budzianowski/multiwoz) (Budzianowski i in., 2018)

In [ ]:
from convlab2.nlu.jointBERT.multiwoz import BERTNLU
from convlab2.util.dataloader.module_dataloader import MultiTurnNLUDataloader
from convlab2.util.dataloader.dataset_dataloader import MultiWOZDataloader

dataloader = MultiTurnNLUDataloader(dataset_dataloader=MultiWOZDataloader())
data = dataloader.load_data(data_key='test', role='sys')['test']

In [ ]:
data['utterance'][:3]

In [ ]:
data['dialog_act'][:3]

Precision, recall oraz F1 obu modeli zmierzymy korzystając z funkcji `evaluate`.

In [ ]:
from convlab2.nlu.evaluate import calculateF1
from tqdm.notebook import tqdm

def evaluate(model, data):
    results = []

    for utt, ctx, acts in tqdm(zip(data['utterance'], data['context'], data['dialog_act']), total=len(data['utterance'])):
        predicted = model.predict(utterance=utt, context=ctx)
        results.append({'predict': predicted, 'golden': acts})

    precision, recall, fscore = calculateF1(results)
    print(f'Precision: {precision:.4f} Recall: {recall:.4f} F1: {fscore:.4f}')
    return precision, recall, fscore

Zmierzmy skuteczność modelu bezkontekstowego.

In [ ]:
noctx_model = BERTNLU(mode='all',
                      config_file='multiwoz_all.json',
                      model_file='https://convlab.blob.core.windows.net/convlab-2/bert_multiwoz_all.zip')

noctx_results = evaluate(noctx_model, data)

Zmierzmy skutecznosć modelu uwzględniającego kontekst.

In [ ]:
ctx_model = BERTNLU(mode='all',
                    config_file='multiwoz_all_context.json',
                    model_file='https://convlab.blob.core.windows.net/convlab-2/bert_multiwoz_all_context.zip')

ctx_results = evaluate(ctx_model, data)

Literatura
----------
 1. Pawel Budzianowski, Tsung-Hsien Wen, Bo-Hsiang Tseng, Iñigo Casanueva, Stefan Ultes, Osman Ramadan, Milica Gasic, MultiWOZ - A Large-Scale Multi-Domain Wizard-of-Oz Dataset for Task-Oriented Dialogue Modelling. EMNLP 2018, pp. 5016-5026